## Some setup

In [40]:
using Logging
using Plots, D4M, StatsBase, Dates, AAUtils, DataFrames, Dash, DashHtmlComponents, DashCoreComponents
gr()
ENV["LINES"] = 900
ENV["COLUMNS"] = 5500
IJulia.set_max_stdio(1 << 200)
;

### We read in our data

In [2]:
CCD1 = ReadCSV("ccd321.csv")
CCD2 = ReadCSV("ccd322.csv")
CCD3 = ReadCSV("ccd323.csv")
CCD4 = ReadCSV("ccd324.csv")
CCD5 = ReadCSV("ccd325.csv")
CCD = CCD1 + CCD2 + CCD3 +CCD4 + CCD5
#CCD = ReadCSV("ccd321.csv")
;

### What vital signs do we have?

In [41]:
tObs = CCD[:,StartsWith("Vital_Signs.Observation.codeDisplay,")]
countVals(tObs)

Dict{SubString{String},Int64} with 5 entries:
  "Abuse_Status_[OMAHA]"                                                          => 677
  "ALT_(Elevated)"                                                                => 166
  "Alanine_aminotransferase_[Enzymatic_activity/volume]_in_Serum_or_Plasma"       => 4
  "Alanine_aminotransferase_[Enzymatic_activity/\u200bvolume]_in_Serum_or_Plasma" => 124
  "AST_(Elevated)"                                                                => 10

In [44]:
tDiagCodes = CCD[:, StartsWith("Diagnostic_Results.Observation.code:,") ]
dDiagCodes = countVals(tDiagCodes)
display(dDiagCodes)
display(sum(values(dDiagCodes)))

Dict{SubString{String},Int64} with 6 entries:
  "20570-8" => 13
  "20565-8" => 10
  "10834-0" => 117
  "18262-6" => 464
  "21000-5" => 322
  "10230-1" => 54

980

In [49]:
tDiagCodeDisplay = CCD[:,StartsWith("Diagnostic_Results.Observation.codeDisplay:,")]
dtDiagCodeDisplay = countVals(tDiagCodeDisplay)
display(dtDiagCodeDisplay)
display(sum(values(dtDiagCodeDisplay)))

Dict{SubString{String},Int64} with 7 entries:
  "Calcium"                                                                       => 206
  "ALT_(Elevated)"                                                                => 4
  "Alanine_aminotransferase_[Enzymatic_activity/volume]_in_Serum_or_Plasma"       => 142
  "Alanine_aminotransferase_[Enzymatic_activity/\u200bvolume]_in_Serum_or_Plasma" => 24
  "Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count"            => 544
  "Appearance_of_Urine"                                                           => 11
  "Cause_of_Death_[US_Standard_Certificate_of_Death]"                             => 49

980

In [50]:
tDiagCodeDisplay1 = tDiagCodeDisplay[getrow(tDiagCodes),:]
dtDiagCodeDisplay1 = countVals(tDiagCodeDisplay1)
display(dtDiagCodeDisplay1)
display(sum(values(dtDiagCodeDisplay1)))

Dict{SubString{String},Int64} with 7 entries:
  "Calcium"                                                                       => 206
  "ALT_(Elevated)"                                                                => 4
  "Alanine_aminotransferase_[Enzymatic_activity/volume]_in_Serum_or_Plasma"       => 142
  "Alanine_aminotransferase_[Enzymatic_activity/\u200bvolume]_in_Serum_or_Plasma" => 24
  "Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count"            => 544
  "Appearance_of_Urine"                                                           => 11
  "Cause_of_Death_[US_Standard_Certificate_of_Death]"                             => 49

980

In [54]:
tCodeNDisplay = tDiagCodes + tDiagCodeDisplay
aa2df(col2type(tCodeNDisplay, ":"))

980×3 DataFrame
│ Row │ Diagnostic_Results.Observation.code  │ Diagnostic_Results.Observation.codeDisplay │ x3                                                                            │
│     │ Union{AbstractString, Number}        │ Union{AbstractString, Number}              │ Union{AbstractString, Number}                                                 │
├─────┼──────────────────────────────────────┼────────────────────────────────────────────┼───────────────────────────────────────────────────────────────────────────────┤
│ 1   │ 0021bca5-354b-49a9-9aac-59061181b00f │ 18262-6                                    │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │
│ 2   │ 0023732c-8b82-4d90-bda4-a085ff824ec6 │ 18262-6                                    │ Calcium                                                                       │
│ 3   │ 002f4670-19c3-4ac9-9da6-833694acc87f │ 20570-8                                    │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │
│ 4   │ 010eab55-0134-4055-ba07-0ec84223ec14 │ 21000-5                                    │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │
│ 5   │ 01753d6e-4d49-4446-a80d-ae939aa3862a │ 18262-6                                    │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │
│ 6   │ 019bb61d-afbd-433f-92df-893b38228c28 │ 21000-5                                    │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │
│ 7   │ 01baef84-b5a7-48ef-aabc-01e1a31cbb5b │ 21000-5                                    │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │
│ 8   │ 020dc3c1-ee6e-483b-8183-1a40091c4c9d │ 21000-5                                    │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │
│ 9   │ 036e006c-24ac-4987-859a-0b8a353ee7e9 │ 10230-1                                    │ Alanine_aminotransferase_[Enzymatic_activity/\u200bvolume]_in_Serum_or_Plasma │
│ 10  │ 03880e56-1dfe-4737-b822-8b44efabdadf │ 21000-5                                    │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │
│ 11  │ 03bc636c-244d-4647-8947-151e2068780f │ 18262-6                                    │ Calcium                                                                       │
│ 12  │ 03d117fc-c459-417c-937a-83c5d2a65b3f │ 18262-6                                    │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │
│ 13  │ 03e16395-75bd-4eaf-aa8a-2fff74e6af85 │ 10834-0                                    │ Alanine_aminotransferase_[Enzymatic_activity/volume]_in_Serum_or_Plasma       │
│ 14  │ 03f0a9a2-8a44-4296-9b48-2a00a27123f5 │ 18262-6                                    │ Calcium                                                                       │
│ 15  │ 044524aa-f602-47e7-8e8f-198f15ecf1bf │ 10834-0                                    │ Alanine_aminotransferase_[Enzymatic_activity/volume]_in_Serum_or_Plasma       │
│ 16  │ 045fa566-ac00-4821-97d2-543caa54fd48 │ 18262-6                                    │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │
│ 17  │ 0467328e-b464-44aa-9fba-1e9546fbf8df │ 18262-6                                    │ Calcium                                                                       │
│ 18  │ 04c192c7-8db2-447f-81bc-76bf51048804 │ 18262-6                                    │ Calcium                                                                       │
│ 19  │ 04f1c4bf-0145-40fe-b96a-211d0953a996 │ 21000-5                                    │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │
│ 20  │ 058aa35b-31e2-41b5-86e0-a7b384005266 │ 10230-1                                    │ Alanine_aminotransferase_[Enzymatic_activity/volume]_in_Serum_or_Plasma       │
│ 21  │ 068a3755-3073-4bdd-a

In [55]:
tDiagCode = CCD[:, "Diagnostic_Results.Observation.code:18262-6," ]
dDiagCode = countVals(tDiagCode)
display(dDiagCode)
display(sum(values(dDiagCode)))

Dict{SubString{String},Int64} with 1 entry:
  "18262-6" => 635

635

In [5]:
tProb = CCD[:,StartsWith("Problems.Observation.codeD,")]
countVals(tProb)

Dict{SubString{String},Int64} with 1 entry:
  "Condition" => 25

In [35]:
comb = tDiag + tProb
aa2df(col2type(comb, ":"))

980×3 DataFrame
│ Row │                                      │ Diagnostic_Results.Observation.codeDisplay                                    │ Problems.Observation.codeDisplay │
│     │ Union{AbstractString, Number}        │ Union{AbstractString, Number}                                                 │ Union{AbstractString, Number}    │
├─────┼──────────────────────────────────────┼───────────────────────────────────────────────────────────────────────────────┼──────────────────────────────────┤
│ 1   │ 0021bca5-354b-49a9-9aac-59061181b00f │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │                                  │
│ 2   │ 0023732c-8b82-4d90-bda4-a085ff824ec6 │ Calcium                                                                       │                                  │
│ 3   │ 002f4670-19c3-4ac9-9da6-833694acc87f │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │                                  │
│ 4   │ 010eab55-0134-4055-ba07-0ec84223ec14 │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │                                  │
│ 5   │ 01753d6e-4d49-4446-a80d-ae939aa3862a │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │                                  │
│ 6   │ 019bb61d-afbd-433f-92df-893b38228c28 │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │                                  │
│ 7   │ 01baef84-b5a7-48ef-aabc-01e1a31cbb5b │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │ Condition                        │
│ 8   │ 020dc3c1-ee6e-483b-8183-1a40091c4c9d │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │                                  │
│ 9   │ 036e006c-24ac-4987-859a-0b8a353ee7e9 │ Alanine_aminotransferase_[Enzymatic_activity/\u200bvolume]_in_Serum_or_Plasma │                                  │
│ 10  │ 03880e56-1dfe-4737-b822-8b44efabdadf │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │                                  │
│ 11  │ 03bc636c-244d-4647-8947-151e2068780f │ Calcium                                                                       │                                  │
│ 12  │ 03d117fc-c459-417c-937a-83c5d2a65b3f │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │                                  │
│ 13  │ 03e16395-75bd-4eaf-aa8a-2fff74e6af85 │ Alanine_aminotransferase_[Enzymatic_activity/volume]_in_Serum_or_Plasma       │                                  │
│ 14  │ 03f0a9a2-8a44-4296-9b48-2a00a27123f5 │ Calcium                                                                       │                                  │
│ 15  │ 044524aa-f602-47e7-8e8f-198f15ecf1bf │ Alanine_aminotransferase_[Enzymatic_activity/volume]_in_Serum_or_Plasma       │                                  │
│ 16  │ 045fa566-ac00-4821-97d2-543caa54fd48 │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │                                  │
│ 17  │ 0467328e-b464-44aa-9fba-1e9546fbf8df │ Calcium                                                                       │                                  │
│ 18  │ 04c192c7-8db2-447f-81bc-76bf51048804 │ Calcium                                                                       │                                  │
│ 19  │ 04f1c4bf-0145-40fe-b96a-211d0953a996 │ Erythrocyte_distribution_width_[Entitic_volume]_by_Automated_count            │                                  │
│ 20  │ 058aa35b-31e2-41b5-86e0-a7b384005266 │ Alanine_aminotransferase_[Enzymatic_activity/volume]_in_Serum_or_Plasma       │                                  │
│ 21  │ 068a3755-3073-4bdd-aaf6-3966336b57e2 │ Alanine_aminotransferase_[Enzymatic_activity/volume]_in_Serum_or_Plasma       │                                  │
│ 22  │ 068cb2ad-988e-4097-9dc3-555ec4c604d9 │ Calcium                                          

In [6]:
tEnc = CCD[:,StartsWith("Encounters.codeDisplay,")]
countVals(tEnc)

Dict{SubString{String},Int64} with 16 entries:
  "Drug_rehabilitation_and_detoxification"                     => 29
  "Asthma_follow-up"                                           => 21
  "Admission_to_thoracic_surgery_department"                   => 9
  "Allergic_disorder_initial_assessment"                       => 10
  "Encounter_for_check_up_(procedure)"                         => 162
  "Emergency_Room_Admission"                                   => 43
  "Emergency_Encounter"                                        => 31
  "Consultation_for_treatment"                                 => 198
  "Allergic_disorder_follow-up_assessment"                     => 19
  "Encounter_for_'check-up'"                                   => 70
  "Domiciliary_or_rest_home_patient_evaluation_and_management" => 15
  "Encounter_for_Problem"                                      => 1
  "Emergency_room_admission_(procedure)"                       => 251
  "Admission_to_surgical_department"                   

In [8]:
AdjObs = tObs * tObs'
aa2df((AdjObs))

981×982 DataFrame. Omitted printing of 842 columns
│ Row │                                      │ 0021bca5-354b-49a9-9aac-59061181b00f │ 0023732c-8b82-4d90-bda4-a085ff824ec6 │ 002f4670-19c3-4ac9-9da6-833694acc87f │ 010eab55-0134-4055-ba07-0ec84223ec14 │ 01753d6e-4d49-4446-a80d-ae939aa3862a │ 019bb61d-afbd-433f-92df-893b38228c28 │ 01baef84-b5a7-48ef-aabc-01e1a31cbb5b │ 020dc3c1-ee6e-483b-8183-1a40091c4c9d │ 036e006c-24ac-4987-859a-0b8a353ee7e9 │ 03880e56-1dfe-4737-b822-8b44efabdadf │ 03bc636c-244d-4647-8947-151e2068780f │ 03d117fc-c459-417c-937a-83c5d2a65b3f │ 03e16395-75bd-4eaf-aa8a-2fff74e6af85 │ 03f0a9a2-8a44-4296-9b48-2a00a27123f5 │ 044524aa-f602-47e7-8e8f-198f15ecf1bf │ 045fa566-ac00-4821-97d2-543caa54fd48 │ 0467328e-b464-44aa-9fba-1e9546fbf8df │ 04c192c7-8db2-447f-81bc-76bf51048804 │ 04f1c4bf-0145-40fe-b96a-211d0953a996 │ 058aa35b-31e2-41b5-86e0-a7b384005266 │ 068a3755-3073-4bdd-aaf6-3966336b57e2 │ 068cb2ad-988e-4097-9dc3-555ec4c604d9 │ 069299d1-acd5-4aa2-9e89-56804a85bdd3 │ 06b51cd9-7beb-40dd-a42c-efaed0b680c7 │ 06e54724-377c-4639-953c-47d3e1ec026c │ 0744266c-1633-4066-9690-0945704bda9d │ 076b50db-644d-44c8-a355-2081913f09d8 │ 076bd25b-2261-4c5d-a34e-d817dce1c39b │ 07c0ee6c-288f-4b66-b6d7-d9ebfd72a40e │ 07f49d1e-0901-4b55-8961-0ed1060a73d5 │ 082c80ed-fab5-4e2a-a5be-9497b68e63a9 │ 082f6151-53e3-4b93-8ee4-32f752fed5bf │ 08701cdb-a8a4-4744-9ee0-04d823b0322f │ 0932283c-e618-4807-bc54-3cdfb61a8924 │ 09544e84-ebd2-4a2a-b9c2-a3ce7c623393 │ 09f00da9-7e9e-4307-999e-2ae771142442 │ 0acc13e9-95ab-4de5-b215-70fca1ada656 │ 0adae0d7-4606-473e-a014-1967585ba3a3 │ 0ae377ef-8dbc-4af1-af61-8007db83c592 │ 0b13c745-6d07-4ca3-8b8b-421dffb8baab │ 0b81da13-2bd0-47f1-a5f2-1aaa3cd6b076 │ 0bb9c9e5-0122-4c99-b2a0-75ffc828af7b │ 0bbd28ba-0978-47a5-92a8-c93b76fed824 │ 0c1b80ea-feb9-4c75-871c-3841d8d1ed99 │ 0ce12127-a681-4894-8ebf-f544f8d9a188 │ 0d2c35ff-71d8-4042-b48b-0e56c12dc48d │ 0df84824-752e-48c8-8d77-84d18162f5dc │ 0ebe7fc8-f50a-412f-9dfe-d24add67b92c │ 0eca62ee-8b04-4ec8-930c-f5b148900a02 │ 0f299176-8dfc-41b1-b6ac-781ddae44211 │ 0f4b6320-4974-4d48-9aba-4e36d6c86353 │ 0f547aca-e664-4422-afce-28d2d6733ee3 │ 0fab7d9c-955e-4c92-8dca-0e4ff795875a │ 0fef42c2-612c-4495-a08c-c6596d720fef │ 0fff0141-66bb-4059-92d2-9d2322e32ecd │ 102065da-61a5-483e-8571-4c8c36a4e88c │ 1049fa65-9917-4524-8229-b0457cf52191 │ 10af6872-d1c7-43b9-82d0-0d57288be070 │ 10b93a33-d452-40f3-98b7-ed16cf678ee4 │ 10bb0cb3-39ab-4062-9d61-102de6058063 │ 10bcb4b0-35c3-482e-b1c5-774efd3c4f1a │ 10c007a2-cac7-479a-a985-de3a0424705b │ 10d9bee3-9255-4b64-a82d-0802636b1850 │ 10e24445-41ec-4380-b86c-e67008a1f677 │ 11091a89-bc83-47fe-89c4-9842786ff37f │ 11c54d3b-63bf-410d-8a5d-3495862ca168 │ 122f38bc-4252-4ee1-82c3-312a55ffd6aa │ 123e8e86-6723-4422-ba49-693ea6a01689 │ 12cfb0b8-9b0b-49ff-967d-eef1b3731d93 │ 12fbc617-77a9-4727-81d4-39c4d4c2b960 │ 1338d6e8-37c8-4dcb-b367-430586c1d1f0 │ 13bf300f-d9b0-4569-a950-6e4c35202219 │ 13c71571-91e6-479e-8360-5faf52e43e68 │ 1435a6a1-d815-459b-8076-4cc424a6416c │ 143bf6a5-50d1-41bd-9bef-4fa756f35cee │ 14564bf6-f73e-4d7a-ad35-523716cd9333 │ 148ee7ab-ae3d-4ff8-bb96-a3ea0b2814fd │ 14a440fb-1085-45f9-baf0-741c61255095 │ 14e88f0d-6c32-40d4-8bf5-210f304c212f │ 1525b6a9-dcdf-45a5-bec5-406ad2abd037 │ 15e91c40-7116-4f82-870c-8810296c9f60 │ 1601d10c-f1dc-4f34-b3ef-694e4b3b8957 │ 16627d1b-b415-406f-80c2-da9f63944cfc │ 16a55126-083d-47b6-ad24-3daf7dcc69bf │ 16b88596-f9a9-424e-ade0-8b176d16a988 │ 1716440b-3474-4fff-8109-0f80e5c328f7 │ 1762208b-3439-4431-b7e7-a0dbf893a0a0 │ 179a4684-63d5-4e8c-923f-c2ae126e4f1b │ 17c77779-eec8-4f12-869e-daa4b6e5a276 │ 18056d0d-da97-4d59-ac93-7c4aac01d5ba │ 18075c49-7216-41fe-8c38-14da3974208b │ 184b4256-832c-4e82-a64d-7f31192f41f3 │ 187da3a2-0c7f-4927-bbb1-70d1de650c37 │ 197132cc-ee42-47d8-bd47-9e282eaf4acb │ 19a37cb5-e219-42f7-abfd-01cd25fb1c15 │ 19d4066f-8891-45c2-8e3f-9d11c135d4f5 │ 1a92c5ce-55e4-4379-8607-89b7e85957a5 │ 1aa5fc92-c8ba-4638-b2fe-8f45b02a38b3 │ 1b510e6b-1e03-4e3a-87e2-9d1defcb6642 │ 1bf9551b-e9af-45d0-8561-5d798d08acd9 │ 1c

In [9]:
tSurg = CCD[:,StartsWith("Surgeries.codeDisplay,")]
rSurg, cSurg, vSurg  = find(col2type(tSurg, ":"))
dSurg = countmap(vSurg)

Dict{SubString{String},Int64} with 29 entries:
  "Alpha-fetoprotein_test"                                                          => 145
  "Percutaneous_mechanical_thrombectomy_of_portal_vein_using_fluoroscopic_guidance" => 1
  "Antenatal_RhD_antibody_screening"                                                => 163
  "Admission_to_orthopedic_department"                                              => 44
  "Medical_induction_of_labor"                                                      => 1
  "Fecal_occult_blood_test"                                                         => 1
  "Admission_to_long_stay_hospital"                                                 => 16
  "Combined_chemotherapy_and_radiation_therapy_(procedure)"                         => 1
  "Admission_to_trauma_surgery_department"                                          => 172
  "Appendectomy"                                                                    => 169
  "Chlamydia_antigen_test"                           

In [10]:
AdjObs1 = AdjObs["0023732c-8b82-4d90-bda4-a085ff824ec6,",:]
AdjObs1[:,"0021bca5-354b-49a9-9aac-59061181b00f,"]

Assoc(Union{AbstractString, Number}["0023732c-8b82-4d90-bda4-a085ff824ec6"], Union{AbstractString, Number}["0021bca5-354b-49a9-9aac-59061181b00f"], Union{AbstractString, Number}[1.0], 
  [1, 1]  =  27.0)